In [1]:
#IBM Applied Data Science Capstone by Marco Pfeiffer

In [2]:
import pandas as pd
import requests
from bs4 import BeautifulSoup
import urllib.request, urllib.parse, urllib.error
import ssl

import numpy as np # library to handle data in a vectorized manner

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

#!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes
#=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [3]:
def getData(url):

    #create connection to url
    html = urllib.request.urlopen(url, context=ctx).read()
    soup = BeautifulSoup(html, 'html.parser')
    
    #read all talbes in list
    tables = soup.find_all("table")
    
    #create empty data array
    data = []

    #read all rows and data of the first table
    for tr in tables[0].find_all('tr'):
        try:
            td = tr.find_all('td')
            
            row = []
            row.append(td[0].text.replace("\n",""))
            row.append(td[1].text.replace("\n","").replace(" 1",""))
            row.append(td[6].text.replace("\n",""))
            
            data.append(row)
             

    

        except: 
            pass

    #create data frame
    df = pd.DataFrame(data, columns = ['Rank', 'City','Size'])
    
    #group array and combine Neighboorhoods
    #df = df.groupby(['PostalCode','Borough'])['Neighborhood'].apply(','.join).reset_index()
    
    return df

In [4]:
def getNearbyVenues(names, latitudes, longitudes, radius=5000, categoryIds=''):
    try:
        venues_list=[]
        for name, lat, lng in zip(names, latitudes, longitudes):
            #print(name)

            # create the API request URL
            url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, VERSION, lat, lng, radius, LIMIT)

            if (categoryIds != ''):
                url = url + '&categoryId={}'
                url = url.format(categoryIds)

            # make the GET request
            response = requests.get(url).json()
            results = response["response"]['venues']

            # return only relevant information for each nearby venue
            for v in results:
                success = False
                try:
                    category = v['categories'][0]['name']
                    success = True
                except:
                    pass

                if success:
                    venues_list.append([(
                        name, 
                        lat, 
                        lng, 
                        v['name'], 
                        v['location']['lat'], 
                        v['location']['lng'],
                        v['categories'][0]['name']
                    )])

        nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
        nearby_venues.columns = ['Location', 
                  'Location Latitude', 
                  'Location Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    except:
        print(url)
        print(response)
        print(results)
        print(nearby_venues)

    return(nearby_venues)

In [5]:
# Ignore SSL certificate errors
ctx = ssl.create_default_context()
ctx.check_hostname = False
ctx.verify_mode = ssl.CERT_NONE

#url = 'https://de.wikipedia.org/wiki/Kanton_(Schweiz)'
url = 'https://de.wikipedia.org/wiki/Liste_der_St%C3%A4dte_in_der_Schweiz'

#create dataframe from url
df = getData(url)

df

Rank                    City     Size
0      1.                  Zürich  396'027
1      2.                    Genf  194'565
2      3.                   Basel  175'131
3      4.                    Bern  140'634
4      5.                Lausanne  135'629
5      6.              Winterthur  106'778
6      7.                  Luzern   81'284
7      8.              St. Gallen   75'310
8      9.                  Lugano   63'668
9     10.             Biel/Bienne   53'667
10    11.                    Thun   43'303
11    12.                   Köniz   39'998
12    13.       La Chaux-de-Fonds   39'027
13    14.                Freiburg   38'288
14    15.            Schaffhausen   35'927
15    16.                    Chur   34'547
16    17.                 Vernier   34'477
17    18.               Neuenburg   33'641
18    19.                   Uster   33'412
19    20.                  Sitten   33'296
20    21.                   Lancy   30'919
21    22.       Yverdon-les-Bains   29'406
22    23.                   Emmen   29'292
23    24.                     Zug   28'603
24    25.                  Kriens   27'229
25    26.     Rapperswil-Jona / 3   26'875
26    27.               Dübendorf   26'759
27    28.                Dietikon   26'277
28    29.                Montreux   26'208
29    30.              Frauenfeld   24'578
30    31.                Wetzikon   23'938
31    32.                     Wil   23'715
32    33.                    Baar   23'228
33    34.                  Meyrin   21'993
34    35.                   Bulle   21'464
35    36.             Kreuzlingen   21'290
36    37.               Wädenswil   21'245
37    38.                 Carouge   20'910
38    39.                  Riehen   20'774
39    40.                  Renens   20'446
40    41.                   Aarau   20'445
41    42.               Allschwil   20'411
42    43.               Wettingen   20'221
43    44.                  Horgen   20'033
44    45.                    Nyon   19'738
45    46.                   Vevey   19'220
46    47.                  Bülach   18'895
47    48.                 Reinach   18'810
48    49.                   Baden   18'670
49    50.                Adliswil   18'448
50    51.              Volketswil   18'437
51    52.                  Kloten   18'373
52    53.                    Onex   18'305
53    54.              Bellinzona   18'131
54    55.                  Gossau   18'053
55    56.               Schlieren   17'905
56    57.                 Thalwil   17'631
57    58.                   Pully   17'624
58    59.           Glarus Nord 5   17'587
59    60.                 Muttenz   17'538
60    61.              Regensdorf   17'478
61    62.                 Monthey   17'409
62    63.                   Olten   17'350
63    64.                Martigny   17'342
64    65.                 Opfikon   17'173
65    66.           Ostermundigen   16'694
66    67.                  Siders   16'547
67    68.               Solothurn   16'545
68    69.                Grenchen   16'480
69    70.            Val-de-Ruz 6   16'399
70    71.       Illnau-Effretikon   16'288
71    72.                Burgdorf   15'998
72    73.              Freienbach   15'981
73    74.                 Locarno   15'803
74    75.             Steffisburg   15'703
75    76.                Pratteln   15'601
76    77.                    Cham   15'523
77    78.                 Herisau   15'512
78    79.                  Morges   15'465
79    80.                  Wohlen   15'446
80    81.             Wallisellen   15'373
81    82.            Langenthal 2   15'316
82    83.               Binningen   15'092
83    84.              Einsiedeln   14'949
84    85.               Mendrisio   14'929
85    86.                Schwyz 2   14'785
86    87.                    Lyss   14'183
87    88.                   Arbon   14'128
88    89.                  Thônex   13'971
89    90.                 Liestal   13'956
90    91.                   Stäfa   13'955
91    92.                Küsnacht   13'849
92    

In [6]:
def get_coords_local(location, output_as='center'):
    """
    get the bounding box of a locality in WGS84 given its name

    Parameters
    ----------
    location : str
        name of the country in english and lowercase
    output_as : 'str
        chose from 'boundingbox' or 'center'. 
         - 'boundingbox' for [latmin, latmax, lonmin, lonmax]
         - 'center' for [latcenter, loncenter]

    Returns
    -------
    output : list
        list with coordinates as str
    """
    # create url
    url = '{0}{1}{2}'.format('http://nominatim.openstreetmap.org/search.php?q=',
                             location+', Schweiz',
                             '&format=json&polygon=0')
    response = requests.get(url).json()[0]

    # parse response to list
    if output_as == 'boundingbox':
        lst = response[output_as]
        output = [float(i) for i in lst]
    if output_as == 'center':
        lst = [response.get(key) for key in ['lat','lon']]
        output = [float(i) for i in lst]
    return output

In [7]:
df2 = df.head(40).copy()

latitudeCln = []
longitudeCln = []
for index, row in df2.iterrows():
    print(row[1])
    lat, long = get_coords_local(location=row[1], output_as='center')
    latitudeCln.append(lat)
    longitudeCln.append(long)

df2['Latitude'] = latitudeCln
df2['Longitude'] = longitudeCln

df2

Zürich
Genf
Basel
Bern
Lausanne
Winterthur
Luzern
St. Gallen
Lugano
Biel/Bienne
Thun
Köniz
La Chaux-de-Fonds
Freiburg
Schaffhausen
Chur
Vernier
Neuenburg
Uster
Sitten
Lancy
Yverdon-les-Bains
Emmen
Zug
Kriens
Rapperswil-Jona / 3
Dübendorf
Dietikon
Montreux
Frauenfeld
Wetzikon
Wil
Baar
Meyrin
Bulle
Kreuzlingen
Wädenswil
Carouge
Riehen
Renens


Rank                 City     Size   Latitude  Longitude
0    1.               Zürich  396'027  47.372394   8.542333
1    2.                 Genf  194'565  46.201756   6.146601
2    3.                Basel  175'131  47.558108   7.587826
3    4.                 Bern  140'634  46.948271   7.451451
4    5.             Lausanne  135'629  46.521827   6.632702
5    6.           Winterthur  106'778  47.499172   8.729150
6    7.               Luzern   81'284  47.050545   8.305468
7    8.           St. Gallen   75'310  47.425059   9.376588
8    9.               Lugano   63'668  46.005010   8.952028
9   10.          Biel/Bienne   53'667  47.140208   7.243903
10  11.                 Thun   43'303  46.758283   7.628086
11  12.                Köniz   39'998  46.922238   7.413058
12  13.    La Chaux-de-Fonds   39'027  47.103287   6.832454
13  14.             Freiburg   38'288  46.678912   7.102711
14  15.         Schaffhausen   35'927  47.696049   8.634513
15  16.                 Chur   34'547  46.855515   9.525407
16  17.              Vernier   34'477  46.213184   6.081576
17  18.            Neuenburg   33'641  46.989583   6.929264
18  19.                Uster   33'412  47.351207   8.717922
19  20.               Sitten   33'296  46.231175   7.358879
20  21.                Lancy   30'919  46.183916   6.122405
21  22.    Yverdon-les-Bains   29'406  46.775852   6.642070
22  23.                Emmen   29'292  47.075243   8.283946
23  24.                  Zug   28'603  47.167990   8.517365
24  25.               Kriens   27'229  47.034146   8.280799
25  26.  Rapperswil-Jona / 3   26'875  47.229828   8.859651
26  27.            Dübendorf   26'759  47.396824   8.618302
27  28.             Dietikon   26'277  47.406883   8.402089
28  29.             Montreux   26'208  46.431083   6.912992
29  30.           Frauenfeld   24'578  47.556236   8.896414
30  31.             Wetzikon   23'938  47.322693   8.798094
31  32.                  Wil   23'715  47.465441   9.042320
32  33.                 Baar   23'228  47.195198   8.525398
33  34.               Meyrin   21'993  46.228323   6.071202
34  35.                Bulle   21'464  46.619097   7.058115
35  36.          Kreuzlingen   21'290  47.646436   9.172562
36  37.            Wädenswil   21'245  47.227884   8.670198
37  38.              Carouge   20'910  46.184669   6.139684
38  39.               Riehen   20'774  47.581693   7.647974
39  40.               Renens   20'446  46.534909   6.592844

In [8]:
address = 'Switzerland'

geolocator = Nominatim(user_agent="explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Switzerland are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Switzerland are 46.7985624, 8.2319736.


In [9]:
# create map of Switzerland using latitude and longitude values
map_switzerland = folium.Map(location=[latitude, longitude], zoom_start=8)

In [10]:
# add markers to map
for lat, lng, local in zip(df2['Latitude'], df2['Longitude'], df2['City']):
    label = '{}'.format(local)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_switzerland)  
    
map_switzerland

In [11]:
CLIENT_ID = '0N2KU1CZHPACA2NNCUDSYL3WMQ2ZKSOZAHYOCA2XL3FFGF2T' # your Foursquare ID
CLIENT_SECRET = 'TN1A2WDP4BCFSVDLRVYO0CVOPKVKUNHMBHGG1E5XXOWLGZIZ' # your Foursquare Secret
VERSION = '20180604'
LIMIT = 30

In [12]:
# Use category id 4bf58dd8d48988d16a941735 to filter for backery
switzerland_venues_backery = getNearbyVenues(names=df2['City'], latitudes=df2['Latitude'], longitudes=df2['Longitude'], radius=1000, categoryIds='4bf58dd8d48988d16a941735')
switzerland_venues_backery.head()

Location  Location Latitude  Location Longitude                  Venue  \
0   Zürich          47.372394            8.542333                Äss-Bar   
1   Zürich          47.372394            8.542333  Confiseur Bachmann AG   
2   Zürich          47.372394            8.542333               Sprüngli   
3   Zürich          47.372394            8.542333               Sprüngli   
4   Zürich          47.372394            8.542333            Brezelkönig   

   Venue Latitude  Venue Longitude Venue Category  
0       47.372561         8.543693         Bakery  
1       47.376582         8.539413         Bakery  
2       47.369398         8.539486   Dessert Shop  
3       47.373842         8.538310   Cupcake Shop  
4       47.373357         8.538118         Bakery

In [13]:
# function to add markers for given venues to map
def addToMap(df, color, existingMap):
    for lat, lng, local, venue, venueCat in zip(df['Venue Latitude'], df['Venue Longitude'], df['Location'], df['Venue'], df['Venue Category']):
        label = '{} ({}) - {}'.format(venue, venueCat, local)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.7).add_to(existingMap)

In [14]:
map_switzerland_backery = folium.Map(location=[latitude, longitude], zoom_start=8)
addToMap(switzerland_venues_backery, 'red', map_switzerland_backery)
map_switzerland_backery

In [15]:
switzerland_venues_universitiy = getNearbyVenues(names=df2['City'], latitudes=df2['Latitude'], longitudes=df2['Longitude'], radius=1000, categoryIds='4d4b7105d754a06372d81259')
switzerland_venues_universitiy.head()

Location  Location Latitude  Location Longitude  \
0   Zürich          47.372394            8.542333   
1   Zürich          47.372394            8.542333   
2   Zürich          47.372394            8.542333   
3   Zürich          47.372394            8.542333   
4   Zürich          47.372394            8.542333   

                                               Venue  Venue Latitude  \
0                                  Zentralbibliothek       47.374171   
1  Bibliothek des Rechtswissenschaftlichen Instit...       47.373268   
2                                     ETH-Bibliothek       47.376619   
3                                      ETH Polysnack       47.376545   
4                         ETH Departement Informatik       47.378292   

   Venue Longitude                Venue Category  
0         8.545037               College Library  
1         8.550828               College Library  
2         8.548579               College Library  
3         8.548674             College Cafeteria  
4         8.548287  College Engineering Building

In [16]:
switzerland_venues_universitiy.shape

(637, 7)

In [17]:
map_switzerland_universitiy = folium.Map(location=[latitude, longitude], zoom_start=8)
addToMap(switzerland_venues_universitiy, 'green', map_switzerland_universitiy)
map_switzerland_universitiy

In [18]:
#get places where people work
switzerland_venues_working_places = getNearbyVenues(names=df2['City'], latitudes=df2['Latitude'], longitudes=df2['Longitude'], radius=1000, categoryIds='4d4b7105d754a06375d81259')
switzerland_venues_working_places.head()

Location  Location Latitude  Location Longitude          Venue  \
0   Zürich          47.372394            8.542333    Fraumünster   
1   Zürich          47.372394            8.542333  Literaturhaus   
2   Zürich          47.372394            8.542333        Rathaus   
3   Zürich          47.372394            8.542333      St. Peter   
4   Zürich          47.372394            8.542333   Grossmünster   

   Venue Latitude  Venue Longitude       Venue Category  
0       47.370098         8.541077               Church  
1       47.371930         8.542780          Event Space  
2       47.371483         8.542719  Government Building  
3       47.371495         8.540753               Church  
4       47.370142         8.543919               Church

In [19]:
switzerland_venues_working_places.shape

(1024, 7)

In [20]:
map_switzerland_working_places = folium.Map(location=[latitude, longitude], zoom_start=8)
addToMap(switzerland_venues_working_places, 'green', map_switzerland_working_places)
map_switzerland_working_places

In [21]:
#Nature & Leisure Locations
switzerland_venues_leisure = getNearbyVenues(names=df2['City'], latitudes=df2['Latitude'], longitudes=df2['Longitude'], radius=1000, categoryIds='4d4b7105d754a06377d81259')
switzerland_venues_leisure.head()

Location  Location Latitude  Location Longitude               Venue  \
0   Zürich          47.372394            8.542333       Rathausbrücke   
1   Zürich          47.372394            8.542333  Rudolf-Brun-Brücke   
2   Zürich          47.372394            8.542333  Kreis 1 - Altstadt   
3   Zürich          47.372394            8.542333           Lindenhof   
4   Zürich          47.372394            8.542333              Zürich   

   Venue Latitude  Venue Longitude    Venue Category  
0       47.371782         8.542279            Bridge  
1       47.374330         8.542451            Bridge  
2       47.374177         8.541146      Neighborhood  
3       47.373005         8.540883  Pedestrian Plaza  
4       47.373082         8.541527              City

In [22]:
switzerland_venues_leisure.shape

(979, 7)

In [23]:
map_switzerland_leisure = folium.Map(location=[latitude, longitude], zoom_start=8)
addToMap(switzerland_venues_leisure, 'green', map_switzerland_leisure)
map_switzerland_leisure

In [24]:
def addColumn(startDf, columnTitle, dataDf):
    grouped = dataDf.groupby('Location').count()
    
    for n in startDf['Location']:
        try:
            startDf.loc[startDf['Location'] == n,columnTitle] = grouped.loc[n, 'Venue']
        except:
            startDf.loc[startDf['Location'] == n,columnTitle] = 0

In [25]:
df2.head()

Rank      City     Size   Latitude  Longitude
0   1.    Zürich  396'027  47.372394   8.542333
1   2.      Genf  194'565  46.201756   6.146601
2   3.     Basel  175'131  47.558108   7.587826
3   4.      Bern  140'634  46.948271   7.451451
4   5.  Lausanne  135'629  46.521827   6.632702

In [28]:
df_data = df2.copy()
df_data.rename(columns={'City':'Location'}, inplace=True)
addColumn(df_data, 'Backery', switzerland_venues_backery)
addColumn(df_data, 'University', switzerland_venues_universitiy)
addColumn(df_data, 'Working', switzerland_venues_working_places)
addColumn(df_data, 'Leisure', switzerland_venues_leisure)
df_data

Rank             Location     Size   Latitude  Longitude  Backery  \
0    1.               Zürich  396'027  47.372394   8.542333     30.0   
1    2.                 Genf  194'565  46.201756   6.146601     30.0   
2    3.                Basel  175'131  47.558108   7.587826     30.0   
3    4.                 Bern  140'634  46.948271   7.451451     30.0   
4    5.             Lausanne  135'629  46.521827   6.632702     30.0   
5    6.           Winterthur  106'778  47.499172   8.729150     11.0   
6    7.               Luzern   81'284  47.050545   8.305468     29.0   
7    8.           St. Gallen   75'310  47.425059   9.376588     20.0   
8    9.               Lugano   63'668  46.005010   8.952028      9.0   
9   10.          Biel/Bienne   53'667  47.140208   7.243903     10.0   
10  11.                 Thun   43'303  46.758283   7.628086      0.0   
11  12.                Köniz   39'998  46.922238   7.413058      4.0   
12  13.    La Chaux-de-Fonds   39'027  47.103287   6.832454      5.0   
13  14.             Freiburg   38'288  46.678912   7.102711      0.0   
14  15.         Schaffhausen   35'927  47.696049   8.634513      5.0   
15  16.                 Chur   34'547  46.855515   9.525407      8.0   
16  17.              Vernier   34'477  46.213184   6.081576      2.0   
17  18.            Neuenburg   33'641  46.989583   6.929264      6.0   
18  19.                Uster   33'412  47.351207   8.717922      4.0   
19  20.               Sitten   33'296  46.231175   7.358879      8.0   
20  21.                Lancy   30'919  46.183916   6.122405     10.0   
21  22.    Yverdon-les-Bains   29'406  46.775852   6.642070      7.0   
22  23.                Emmen   29'292  47.075243   8.283946      3.0   
23  24.                  Zug   28'603  47.167990   8.517365     16.0   
24  25.               Kriens   27'229  47.034146   8.280799      6.0   
25  26.  Rapperswil-Jona / 3   26'875  47.229828   8.859651      0.0   
26  27.            Dübendorf   26'759  47.396824   8.618302      5.0   
27  28.             Dietikon   26'277  47.406883   8.402089      6.0   
28  29.             Montreux   26'208  46.431083   6.912992      5.0   
29  30.           Frauenfeld   24'578  47.556236   8.896414     10.0   
30  31.             Wetzikon   23'938  47.322693   8.798094      3.0   
31  32.                  Wil   23'715  47.465441   9.042320      7.0   
32  33.                 Baar   23'228  47.195198   8.525398      5.0   
33  34.               Meyrin   21'993  46.228323   6.071202      3.0   
34  35.                Bulle   21'464  46.619097   7.058115      6.0   
35  36.          Kreuzlingen   21'290  47.646436   9.172562      6.0   
36  37.            Wädenswil   21'245  47.227884   8.670198      4.0   
37  38.              Carouge   20'910  46.184669   6.139684     25.0   
38  39.               Riehen   20'774  47.581693   7.647974      2.0   
39  40.               Renens   20'446  46.534909   6.592844     10.0   

    University  Working  Leisure  
0         30.0     30.0     30.0  
1         30.0     29.0     30.0  
2         30.0     30.0     30.0  
3         28.0     30.0     30.0  
4         28.0     30.0     29.0  
5         30.0     29.0     30.0  
6         28.0     30.0     30.0  
7         26.0     28.0     29.0  
8         29.0     30.0     30.0  
9         27.0     29.0     30.0  
10        18.0     24.0     27.0  
11         6.0     28.0     18.0  
12         6.0     23.0     22.0  
13         0.0      1.0      3.0  
14        13.0     27.0     28.0  
15        20.0     26.0     28.0  
16         0.0     26.0     11.0  
17        30.0     26.0     29.0  
18         9.0     24.0     25.0  
19        11.0     21.0     23.0  
20        16.0     29.0     26.0  
21        14.0     28.0     29.0  
22         6.0     27.0     22.0  
23        24.0     30.0     30.0  
24         6.0     28.0     23.0  
25         0.0     11.0      2.0  
26         9.0     27.0     19.0  
27        11.0     27.0     28.0  
28        30.0     23.0     30.0  


In [29]:
# negative weight, because Mario wants to open a backery and thus wants to avoid concurrence as much as possible
weight_backery = -1

# positive weight, because uni students are good customers
weight_uni = 1

# positive weight because employees are even better customers
weight_offices = 2

# positive weight, because it is good being loacated to a leisure / nature spot
weight_leisure = 1

In [30]:
df_weighted = df_data[['Location']].copy()

In [31]:
df_weighted['Score'] = df_data['Backery'] * weight_backery + df_data['University'] * weight_uni + df_data['Working'] * weight_offices + df_data['Leisure'] * weight_leisure
df_weighted = df_weighted.sort_values(by=['Score'], ascending=False)
df_weighted

Location  Score
8                Lugano  110.0
5            Winterthur  107.0
9           Biel/Bienne  105.0
17            Neuenburg  105.0
28             Montreux  101.0
23                  Zug   98.0
37              Carouge   94.0
10                 Thun   93.0
21    Yverdon-les-Bains   92.0
15                 Chur   92.0
7            St. Gallen   91.0
0                Zürich   90.0
14         Schaffhausen   90.0
32                 Baar   90.0
20                Lancy   90.0
2                 Basel   90.0
6                Luzern   89.0
1                  Genf   88.0
3                  Bern   88.0
27             Dietikon   87.0
4              Lausanne   87.0
31                  Wil   87.0
35          Kreuzlingen   84.0
34                Bulle   80.0
22                Emmen   79.0
24               Kriens   79.0
18                Uster   78.0
39               Renens   77.0
26            Dübendorf   77.0
33               Meyrin   76.0
11                Köniz   76.0
29           Frauenfeld   72.0
12    La Chaux-de-Fonds   69.0
30             Wetzikon   68.0
19               Sitten   68.0
36            Wädenswil   64.0
16              Vernier   61.0
38               Riehen   53.0
25  Rapperswil-Jona / 3   24.0
13             Freiburg    5.0

In [40]:
map_result = folium.Map(location=[latitude, longitude], zoom_start=11)

winner = df2[df2['City'] == 'Lugano']

for lat, lng, local in zip(winner['Latitude'], winner['Longitude'], winner['City']):
    label = '{}'.format(local)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='blue',
        fill_opacity=0.7).add_to(map_result) 

addToMap(switzerland_venues_backery[switzerland_venues_backery['Location'] == 'Lugano'], 'red', map_result)
addToMap(switzerland_venues_leisure[switzerland_venues_leisure['Location'] == 'Lugano'], 'gold', map_result)
addToMap(switzerland_venues_working_places[switzerland_venues_working_places['Location'] == 'Lugano'], 'green', map_result)
addToMap(switzerland_venues_universitiy[switzerland_venues_universitiy['Location'] == 'Lugano'], 'orange', map_result)

map_result